# Recommender Systems 3 - Content-based Filtering

### Import libraries

In [1]:
import pandas as pd
import string
from pprint import pprint
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

### Load data

In [2]:
all_songs = pd.read_csv('data/songdata.csv')
all_songs.shape

(57650, 4)

### Examine data

In [3]:
pd.set_option('max_colwidth', None)

In [4]:
# Display first few rows
all_songs.head()

artist                   song                                        link  \
0   ABBA  Ahe's My Kind Of Girl  /a/abba/ahes+my+kind+of+girl_20598417.html   
1   ABBA       Andante, Andante       /a/abba/andante+andante_20002708.html   
2   ABBA         As Good As New        /a/abba/as+good+as+new_20003033.html   
3   ABBA                   Bang                  /a/abba/bang_20598415.html   
4   ABBA       Bang-A-Boomerang      /a/abba/bang+a+boomerang_20002668.html   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           text  
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 Look at her face, it's a wonderful face  \nAnd it means something special to me  \nLook at the way that she smiles when she sees me  \nHow lucky can one fellow be?  \n  \nShe's just my kind of girl, she makes me feel fine  \nWho could ever believe that she could be mine?  \nShe's just my kind of girl, without her I'm blue  \nAnd if she ever leaves me what could I do, what could I do?  \n  \nAnd when we go for a walk in the park  \nAnd she holds me and squeezes my hand  \nWe'll go on walking for hours and talking  \nAbout all the things that we plan  \n  \nShe's just my kind of girl, she makes me feel fine  \nWho could ever believe that she could be mine?  \nShe's just my kind of girl, without her I'm blue  \nAnd if she ever leaves me what could I do, what could I do?\n\n  
1                               Take it easy with me, please  \nTouch me gently like a summer evening breeze  \nTake your time, make it slow  \nAndante, Andante  \nJust let the feeling grow  \n  \nMake your fingers soft and light  \nLet your body be the velvet of the night  \nTouch my soul, you know how  \nAndante, Andante  \nGo slowly with me now  \n  \nI'm your music  \n(I am your music and I am your song)  \nI'm your song  \n(I am your music and I am your song)  \nPlay me tim

### Preprocess data

In [5]:
# Prepare smaller data subset of first 5,000 songs and drop column 'link'
songs = all_songs.head(5000).drop('link', axis=1).reset_index(drop=True)
songs.shape

(5000, 3)

In [6]:
# Choose a test song name
TEST_SONG_NAME = 'Wayfaring Stranger'

# Get test song index
TEST_SONG_INDEX = songs.loc[songs['song']==TEST_SONG_NAME].index.values[0].astype(int).item()

# Display test song row
songs.loc[songs['song']==TEST_SONG_NAME]

artist                song  \
4653  Ed Sheeran  Wayfaring Stranger   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             text  
4653  I am a poor, wayfaring Stranger  \nTraveling through this world alone  \nThere's no sickness, toil or danger  \nIn that bright land, to which I go  \nI'm going there to see my mother  \nI'm going there no more to roam  \nI'm only going over Jordan  \nI'm only going over home now  \n  \n(Hey-ey-ey yeah...)  \n  \nAnd I know dark clouds, will gather me  \nAnd I know my way, is rough and steep  \nAnd the beautiful fields lie just beyond me  \n  \nAnd I know my way, is rough and steep  \nI'm going there to see my mother  \nAnd I'm going there no more to roam  \nI'm only going over Jordan  \nI'm only going over home now  \n  \nCause I am a poor, wayfaring Stranger  \nTraveling through this world alone  \nThere's no sickness, toil or danger  \nIn that bright land, to which I go  \nI'm going there to see my mother  \nAnd I'm going there no more to roam  \nI'm only going over Jordan  \nI'm only going over home now\n\n

##### Note the order of text cleanup steps

In [7]:
# Cleanup data: remove newline characters
songs['text_clean'] = songs['text'].str.replace(r'\n', '', regex=True)

# Display test song lyrics after 1st cleanup step
songs['text_clean'][TEST_SONG_INDEX]

"I am a poor, wayfaring Stranger  Traveling through this world alone  There's no sickness, toil or danger  In that bright land, to which I go  I'm going there to see my mother  I'm going there no more to roam  I'm only going over Jordan  I'm only going over home now    (Hey-ey-ey yeah...)    And I know dark clouds, will gather me  And I know my way, is rough and steep  And the beautiful fields lie just beyond me    And I know my way, is rough and steep  I'm going there to see my mother  And I'm going there no more to roam  I'm only going over Jordan  I'm only going over home now    Cause I am a poor, wayfaring Stranger  Traveling through this world alone  There's no sickness, toil or danger  In that bright land, to which I go  I'm going there to see my mother  And I'm going there no more to roam  I'm only going over Jordan  I'm only going over home now"

In [8]:
# Create function to remove punctuation and lowercase all text
def cleanup_text(text):
    text = "".join([word.lower() for word in text if word not in string.punctuation])
    text = ' '.join(text.split())
    return text

In [9]:
# Remove punctuation and lowercase all text
songs['text_clean'] = songs['text'].apply(lambda x: cleanup_text(x))

# Display test song lyrics after 2nd cleanup step
songs['text_clean'][TEST_SONG_INDEX]

'i am a poor wayfaring stranger traveling through this world alone theres no sickness toil or danger in that bright land to which i go im going there to see my mother im going there no more to roam im only going over jordan im only going over home now heyeyey yeah and i know dark clouds will gather me and i know my way is rough and steep and the beautiful fields lie just beyond me and i know my way is rough and steep im going there to see my mother and im going there no more to roam im only going over jordan im only going over home now cause i am a poor wayfaring stranger traveling through this world alone theres no sickness toil or danger in that bright land to which i go im going there to see my mother and im going there no more to roam im only going over jordan im only going over home now'

### Run TF-IDF vectorizer

In [10]:
# Instantiate TF-IDF vectorizer
tfidf = TfidfVectorizer(analyzer='word', stop_words='english')

In [11]:
# Create a song lyrics matrix for each word and its TF-IDF score with regard to each song lyric
lyrics_matrix = tfidf.fit_transform(songs['text_clean'])
lyrics_matrix

<5000x22583 sparse matrix of type '<class 'numpy.float64'>'
	with 260298 stored elements in Compressed Sparse Row format>

### Generate similarities matrix (on lyrics) to make recommendations

In [12]:
# Calculate the cosine similarity of each item with every other item in the dataset
cosine_similarities = cosine_similarity(lyrics_matrix)
cosine_similarities.shape

(5000, 5000)

In [13]:
cosine_similarities

array([[1.        , 0.00477314, 0.0083177 , ..., 0.03102084, 0.04599649,
        0.08686959],
       [0.00477314, 1.        , 0.00441034, ..., 0.00274612, 0.01548965,
        0.00803848],
       [0.0083177 , 0.00441034, 1.        , ..., 0.0055905 , 0.00494984,
        0.02107475],
       ...,
       [0.03102084, 0.00274612, 0.0055905 , ..., 1.        , 0.01033882,
        0.01254818],
       [0.04599649, 0.01548965, 0.00494984, ..., 0.01033882, 1.        ,
        0.07294173],
       [0.08686959, 0.00803848, 0.02107475, ..., 0.01254818, 0.07294173,
        1.        ]])

In [14]:
# Print cosine_similarities row for test song
cosine_similarities[TEST_SONG_INDEX]

array([0.0327795 , 0.01298228, 0.00597844, ..., 0.        , 0.        ,
       0.06066757])

#### argsort performs an indirect sort on a numpy array
 * It returns an array of indicies in sorted order

In [15]:
# Print index values for cosine_similarities row for test song
cosine_similarities[TEST_SONG_INDEX].argsort()

array([1811, 2704, 1114, ..., 1621, 3455, 4653])

In [16]:
# Print top 10 indicies from cosine_similarities row for test song in descending sorted order
#  -1 in the notation [:-10:-1] means to reverse the list
cosine_similarities[TEST_SONG_INDEX].argsort()[:-10:-1]

array([4653, 3455, 1621, 3977, 3325, 1507, 1798, 1489, 4277])

In [17]:
%%time

# Store the names of the 50 most similar songs for each song in our dataset
similarities = {}
for i in range(len(cosine_similarities)):
    # Sort each element in cosine_similarities and get the indexes of the 50 most similar songs
    similar_indices = cosine_similarities[i].argsort()[:-50:-1]
    
    # Store in similarities each name of the 50 most similar songs
    # Note: the first one is the same song
    similarities[songs['song'].iloc[i]] = [(cosine_similarities[i][x], songs['song'][x], songs['artist'][x])
                                           for x in similar_indices][1:]

CPU times: user 4.16 s, sys: 84.5 ms, total: 4.24 s
Wall time: 4.42 s


In [18]:
pprint(similarities)

{"'Disco' La Passione": [(0.46487930422059837, 'People Need Love', 'ABBA'),
                         (0.45997121163749016, 'Tragedy', 'Christina Perri'),
                         (0.45970124504147636,
                          'La La I Love You',
                          'Don McLean'),
                         (0.4571471534511741, 'Caravan', 'Counting Crows'),
                         (0.4532138907789168, 'I Love You', 'Avril Lavigne'),
                         (0.4522255678969942, 'Love Street', 'Doors'),
                         (0.4491575367944892, 'Move On', 'ABBA'),
                         (0.43483963927741276, 'Kiss Me', 'Avril Lavigne'),
                         (0.4214938465928529,
                          'Baby Come Out Tonight',
                          'Dolly Parton'),
                         (0.4212773861673884,
                          'Let Me In Your Life',
                          'Bill Withers'),
                         (0.4206556645773351, 'Katmandu', 'Cat Stev

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[(0.2876213695773306, 'Bad Girl', 'Conway Twitty'),
                             (0.23650719596384892,
                              'More Today Than Yesterday',
                              'Andy Williams'),
                             (0.22887430102981118,
                              'No Matter What',
                              'Def Leppard'),
                             (0.2147183098854974, 'Famous Girl', 'Chris Brown'),
                             (0.21416716320603, 'Over The Mountains', 'Bosson'),
                             (0.21252532437533408,
                              'By The Time I Get To Phoenix',
                              'Conway Twitty'),
                             (0.2118459736960166, 'Dan Dare', 'Elton John'),
                             (0.20988212374006426,
                              'Heaven Or Hell',
                              'Alphaville'),
                             (0.20437720519401767,
                              'The End Of The Worl

In [19]:
similarities['Thunder Road']

[(0.4294435625120198, "It's Alright", 'Chicago'),
 (0.3102155162822936, 'Anyway You Want', 'Chicago'),
 (0.2952835232208692, 'All About You', 'Bruno Mars'),
 (0.29221829522496573, "I Can't Understand It", 'Cheap Trick'),
 (0.27900959799728525, 'Smile', 'Avril Lavigne'),
 (0.2666647633871728, 'Voices In My Head', 'Bruno Mars'),
 (0.24785596581583508, 'Better', 'Britney Spears'),
 (0.24720978307477148, 'Touch And Go', 'Ed Sheeran'),
 (0.24527434076344454, 'Moses', 'Coldplay'),
 (0.24335892402361922, 'Kneel And Pray', 'Deep Purple'),
 (0.23724537846273644, "It's Alright Now", 'Cliff Richard'),
 (0.23629457814963084, 'Rock N Roll', 'Avril Lavigne'),
 (0.23614583109955922, 'American Night', 'Doors'),
 (0.23487608884337663, 'Oh Well', 'Depeche Mode'),
 (0.2308450421103696, 'Have A Heart', 'Bonnie Raitt'),
 (0.2229485427260377, "You're So Beautiful", 'Def Leppard'),
 (0.22255057760973154, "She Don't Want Nobody Near", 'Counting Crows'),
 (0.2177348521576758, 'Above The Clouds', 'Electric Ligh

### Create song recommender

In [20]:
# Use the similarity scores (generated above) to access the most similar items and make recommendations
# Create Content based recommender class
class ContentBasedRecommender:
    def __init__(self, matrix):
        self.matrix_similar = matrix

    def _print_songs(self, song, recom_songs):
        rec_items = len(recom_songs)
        
        print(f'The {rec_items} recommended songs for {song} are:')
        for i in range(rec_items):
            print(f"\t{i+1}: {recom_songs[i][1]} by {recom_songs[i][2]} (with {round(recom_songs[i][0], 3)}" +
                   " similarity score)")
        
    def recommend(self, song, rec_num_songs=5):
        recom_songs = self.matrix_similar[song][:rec_num_songs]
        # Print each recommend song
        self._print_songs(song=song, recom_songs=recom_songs)

In [21]:
# Instantiate Content based recommender class with the precomputed similarities
recommedations = ContentBasedRecommender(similarities)

### Make song recommendations

#### Sample song indexes
* 2106 : Winter Wonderland
* 465  : The Turn Of A Friendly Card (Part 1)
* 695  : Take It Easy
* 171  : My Girl

In [22]:
# Pick another song and make a recommendation
recommedations.recommend(songs['song'].iloc[2106], 3)

The 3 recommended songs for Winter Wonderland are:
	1: Winter Wonderland by Andy Williams (with 0.967 similarity score)
	2: Winter Wonderland by Air Supply (with 0.922 similarity score)
	3: Winter Wonderland by Bryan White (with 0.751 similarity score)


In [23]:
# Pick a song and make a recommendation
recommedations.recommend(songs['song'].iloc[465])

The 5 recommended songs for The Turn Of A Friendly Card (Part 1) are:
	1: The Turn Of A Friendly Card by Alan Parsons Project (with 0.625 similarity score)
	2: The Turn Of A Friendly Card (Part One) by Alan Parsons Project (with 0.621 similarity score)
	3: Home Truth by Elvis Costello (with 0.194 similarity score)
	4: Percy's Song by Arlo Guthrie (with 0.159 similarity score)
	5: Go Insane by Doors (with 0.15 similarity score)


In [24]:
# Pick another song and make a recommendation
recommedations.recommend(songs['song'].iloc[695], 4)

The 4 recommended songs for Take It Easy are:
	1: Easy To Be Hard by Cher (with 0.4 similarity score)
	2: Girls It Ain't Easy by Dusty Springfield (with 0.396 similarity score)
	3: Let Me Down Easy by Dusty Springfield (with 0.369 similarity score)
	4: It Ain't Gonna Be Easy by Elton John (with 0.367 similarity score)


In [25]:
# Pick another song and make a recommendation
recommedations.recommend(songs['song'].iloc[171], 6)

The 6 recommended songs for My Girl are:
	1: Another Girl by The Beatles (with 0.322 similarity score)
	2: Bad Girl by Conway Twitty (with 0.3 similarity score)
	3: Famous Girl by Chris Brown (with 0.295 similarity score)
	4: No Matter What by Def Leppard (with 0.289 similarity score)
	5: Top Of The World by Bruno Mars (with 0.266 similarity score)
	6: I Got The Girl by Bon Jovi (with 0.256 similarity score)
